# Generate Sankey Diagram for each item

#### Import required modules

In [ ]:
import numpy as np
import pandas as pd
from copy import deepcopy
from pathlib import Path
from datetime import datetime
import matplotlib.pyplot as plt
import plotly.offline as py
import plotly.graph_objects as go
from IPython.display import Image
import ipywidgets as widgets
from ipywidgets import interact, interact_manual

#### Configure viewing settings

In [ ]:
pd.set_option('display.max_rows', 500)
pd.set_option('display.max_columns', 500)
pd.set_option('display.width', 1000)

## [Graph Theory](https://medium.com/basecs/a-gentle-introduction-to-graph-theory-77969829ead8) for Network Management

Given a dataset, reduce it to a weighted directed graph by corporation and display the relationships.

In [ ]:
cfd = pd.read_csv('lift.csv')
cfd.head()

In [ ]:
def generate_sankey(antecedent, top_n):
    """ Interactive selection of the top_n consequents for an antecedent displayed in a Sankey graph."""
    
    # Hide pandas chaining warning (not required)
    pd.options.mode.chained_assignment = None
    
    #Filter data by consequent and top number
    x = cfd.loc[cfd.antecedents == antecedent, :].sort_values(by=['lift'], ascending=False)
    x = x[['antecedents','consequents','lift']]
    x = x.head(top_n)
    
    # Create generic columns
    column_names = ['X','Y','Z']
    x.columns = column_names

    # Unique list of antecedent/consequent names (nodes) for confidence ######
    ant_names = set(x['X'].tolist())
    cons_names = set(x['Y'].tolist())
    nodes = list(set(list(ant_names) + list(cons_names)))
    
    # Map nodes to values
    name_map = { item : index for index, item in enumerate(nodes) }
    x.loc[:,'X_ID'] = x["X"].map(name_map)
    x.loc[:,'Y_ID'] = x["Y"].map(name_map)
    
    # Generate the Sankey diagram
    fig = go.Figure(data=[go.Sankey(
        node = dict(
          pad = 30,
          thickness = 20,
          line = dict(color = "black", width = .2),
          label = nodes,
          #color = colors
        ),
        link = dict(
          source = x['X_ID'].tolist(), # indices correspond to consequent labels
          target = x['Y_ID'].tolist(), # indices antecedent to consequent labels
          value = x['Z'].tolist() # Confidences
      ))])    

    # Graph title
    title_text = f'lift of Top {top_n} Consequents by {antecedent}'
    
    # Update graph
    fig.update_layout(title_text=title_text,
                     bargap=1,
                     boxgap=1,
                     funnelgap=1,
                     width=700,
                     font=dict(size=9),
                     titlefont=dict(size=20),
                     showlegend=True
                     )
    
    # Display graph
    fig.show()


_ = interact(generate_sankey,
         antecedent = widgets.Dropdown(
             options = sorted(cfd['antecedents'].unique().tolist(),reverse=False),
             value = sorted(cfd['antecedents'].unique().tolist(),reverse=False)[0]
         ),
         top_n = widgets.IntSlider(
             value = 5,
             min = 0,
             max = 100,
             step = 5,
             description='Top n:',
             disabled=False,
             continuous_update=False,
             orientation='horizontal',
             readout=True,
             readout_format='d'
         )
        )